# Carbon + Census Interactive Visualization Tool

1. Carbon Emission
2. Carbon + Census 
3. Spatial Grouping

Note: If you encounter errors while playing with interactive plots, it is most likely due to the incompletion of the data. You can try to select different variables or adjust the year slider.

Google Slides - https://docs.google.com/presentation/d/18ySA4V40iqT7bUT5-Phz6Eb73N8SURFQhbhChV0D-H4/edit#slide=id.gbb3da7b5ee_0_11

In [1]:
import pandas as pd
import numpy as np
import json
import urllib.request
import pinyin
from itertools import compress
import pprint

import ipywidgets as widgets
from __future__ import print_function
from ipywidgets import interact, interactive, fixed, interact_manual

import matplotlib.pyplot as plt

import plotly.graph_objects as go
import plotly.express as px
from plotly.subplots import make_subplots
from plotly.offline import download_plotlyjs, init_notebook_mode,  iplot
from plotly.graph_objs import Contours, Histogram2dContour, Marker, Scatter
init_notebook_mode(connected=True)

In [2]:
# Token or credentials
MAPBOX_TOKEN = open('credentials/mapbox.txt').read().rstrip()

In [3]:
EMISSION_PATH = 'data/china_emission.xlsx'
SINK_PATH = 'data/省级碳汇和生态元数据.xlsx'
PP_PATH = 'data/china_stats_gov_provincial_data_master.xlsx'
GROUP_PATH = 'data/china_province_grouping.xlsx'
CHINA_GEOJSON = 'data/china-province-simplified.geojson'

In [4]:
# Access China boundary data - geojson format
with open(CHINA_GEOJSON, 'r', encoding='UTF-8') as j:
     jdata = json.loads(j.read())

# Check the naming system
n_ROI = len(jdata['features']) # number of ROIs
locations = [k for k in range(n_ROI)]
text = [feat['properties']['NAME']  for feat in jdata['features'] if feat['id'] in locations] #province names
# print(text)

In [5]:
# Carbon emission
# Query values 
df_emission = pd.read_excel(EMISSION_PATH, 'master')
df_emission = df_emission[df_emission['type']=='总排放（万吨CO2）'].iloc[:,1:]
df_emission = df_emission.drop('type', axis=1)

# Add missing provinces 
df_emission_copy = df_emission
miss_ROIs = ['西藏自治区','香港','澳门','台湾']
df_emission_copy[miss_ROIs] = np.nan

# Calculate mean values 
emission_mean_copy = df_emission_copy.iloc[:, 1:].mean(axis=0)

In [6]:
# Carbon sink
# Query values 
df_sink = pd.read_excel(SINK_PATH,'碳汇')
df_sink = df_sink.T.reset_index()
df_sink.columns = ['year'] + list(df_sink.iloc[0, 1:])
df_sink = df_sink[1:]

# Add missing provinces 
df_sink_copy = df_sink
miss_ROIs = ['西藏自治区','香港','澳门','台湾']
df_sink_copy[miss_ROIs] = np.nan

# Calculate mean values 
sink_mean_copy = df_sink_copy.iloc[:, 1:].mean(axis=0)

In [7]:
# Census data
df_PP = pd.read_excel(PP_PATH)

# Add missing provinces 
df_PP_copy = df_PP
miss_ROIs = ['香港','澳门','台湾']
df_PP_copy[miss_ROIs] = np.nan

In [8]:
fids_lv4 = list(set(df_PP_copy[df_PP_copy.columns[4]]))
sel = ['生产总值' in i for i in set(df_PP_copy[df_PP_copy.columns[4]])]
re = list(compress(fids_lv4, sel))
# re

In [9]:
# Spatial clusters
df_group = pd.read_excel(GROUP_PATH)
df_group_copy = df_group
df_group_copy.columns = df_group_copy.columns.drop('Province').insert(0, 'name')
# df_group_copy.head(5)

In [10]:
df_flow = (df_sink_copy - df_sink_copy.shift()) * 44 / 12
df_flow['year'] = df_sink_copy['year'].values
df_flow = df_flow.iloc[1:, :].reset_index(drop=True)
df_flow_copy = df_flow
# df_flow_copy.head(5)


In [11]:
# Average carbon flow from 2001 to 2017
flow_mean_copy = df_flow_copy.iloc[:, 1:].mean(axis=0)
# flow_mean_copy

In [12]:
provinces = ['year'] + df_emission_copy.columns.drop('year').to_list()
df_emission_01 = df_emission_copy.iloc[6:, :].reindex(provinces, axis=1).reset_index(drop=True)
df_flow_01 = df_flow_copy.reindex(provinces, axis=1).reset_index(drop=True)

In [13]:
# Calculate net carbon emission  

# Sunstract mean carbon flow from 2001 to 2017 from anual carbon emission
df_net_01 = df_emission_01
for x in df_emission_01.columns.drop('year'):
    df_net_01[x] = df_emission_01[x] - df_flow_copy[x].mean() * 100

# Substract annual carbon flow from annual carbon emission
# df_net_01 = df_emission_01.iloc[:, 1:] - df_flow_01.iloc[:, 1:] * 100
# df_net_01 = df_net_01.set_index(df_emission_01.year).reset_index()

# df_net_01

In [14]:
# Query GDP and population from 2001 to 2017
START_YEAR = 2001
END_YEAR = 2017
df_gdpTotal_all =  df_PP_copy.loc[(df_PP_copy['lv4']=='地区生产总值(亿元)'), df_PP_copy.columns[5:]].reset_index(drop=True)
df_gdpTotal_01 = df_PP_copy.loc[(df_PP_copy['lv4']=='地区生产总值(亿元)') & (df_PP_copy['year']<=END_YEAR) & (df_PP_copy['year']>=START_YEAR), df_PP_copy.columns[5:]].reset_index(drop=True)
# df_gdpTotal_01

In [15]:
df_pop_all = df_PP_copy.loc[(df_PP_copy['lv3']=='人口数(人口抽样调查)') & (df_PP_copy['lv4']=='人口数(人口抽样调查)(人)'), df_PP_copy.columns[5:]].reset_index(drop=True)
df_pop_01 = df_PP_copy.loc[(df_PP_copy['lv3']=='人口数(人口抽样调查)') & (df_PP_copy['lv4']=='人口数(人口抽样调查)(人)') & (df_PP_copy['year']<=END_YEAR) & (df_PP_copy['year']>=START_YEAR), df_PP_copy.columns[5:]].reset_index(drop=True)
# df_pop_01

In [16]:
# Net carbon emission per capita
df_net_01_perCap = (df_net_01.set_index('year') / df_pop_01.set_index('year')).reset_index()
df_net_01_perCap_copy = df_net_01_perCap
# df_net_01_perCap_copy

In [17]:
# Total carbon emission per capita
df_net_01_gdpTotal = (df_net_01.set_index('year') / df_gdpTotal_01.set_index('year')).reset_index()
df_net_01_gdpTotal_copy = df_net_01_gdpTotal
# df_net_01_gdpTotal_copy

In [18]:
df_total_01_perCap = (df_emission_01.set_index('year') / df_pop_01.set_index('year')).reset_index()
df_total_01_perCap_copy = df_total_01_perCap
# df_total_01_perCap_copy

In [19]:
df_total_all_perCap = (df_emission_copy.set_index('year') / df_pop_all.set_index('year')).reset_index()
df_total_all_perCap_copy = df_total_all_perCap
# df_total_all_perCap_copy

In [20]:
df_total_01_gdpTotal = (df_emission_01.set_index('year') / df_gdpTotal_01.set_index('year')).reset_index()
df_total_01_gdpTotal_copy = df_total_01_gdpTotal
# df_total_01_gdpTotal_copy

In [21]:
df_total_all_gdpTotal = (df_emission_copy.set_index('year') / df_gdpTotal_all.set_index('year')).reset_index()
df_total_all_gdpTotal_copy = df_total_all_gdpTotal
# df_total_all_gdpTotal_copy

In [22]:
# Unify dataset
df_total_all_gdpTotal_copy = df_total_all_gdpTotal.melt(id_vars=['year'])
df_total_all_gdpTotal_copy.columns = ['year', 'name', 'value']
df_total_all_gdpTotal_copy['variable'] = 'totalEmission_gdpTotal(万吨/亿元)'

df_net_01_gdpTotal_copy = df_net_01_gdpTotal.melt(id_vars=['year'])
df_net_01_gdpTotal_copy.columns = ['year', 'name', 'value']
df_net_01_gdpTotal_copy['variable'] = 'netEmission_gdpTotal(万吨/亿元)'

df_total_all_perCap_copy = df_total_all_perCap.melt(id_vars=['year'])
df_total_all_perCap_copy.columns = ['year', 'name', 'value']
df_total_all_perCap_copy['variable'] = 'totalEmission_perCap(万吨/人)'

df_net_01_perCap_copy = df_net_01_perCap.melt(id_vars=['year'])
df_net_01_perCap_copy.columns = ['year', 'name', 'value']
df_net_01_perCap_copy['variable'] = 'netEmission_perCap(万吨/人)'

df_carbon_all_perCap_gdpTotal_copy = pd.concat([df_total_all_gdpTotal_copy, df_net_01_gdpTotal_copy, df_total_all_perCap_copy, df_net_01_perCap_copy])
# df_carbon_all_perCap_gdpTotal_copy

### Ranking of carbon emission

In [23]:
# Data pre-processing 
# Mean total carbon emission from 2001 to 2017
emission_mean_01 =  df_emission_copy.loc[(df_emission_copy['year']>=2001) & (df_emission_copy['year']<=2017), df_emission_copy.columns.drop('year')].mean(axis=0)
df_emission_mean_copy = pd.DataFrame(emission_mean_01).reset_index()
df_emission_mean_copy.columns = ['name', 'value']
df_emission_mean_copy = df_emission_mean_copy.sort_values(by='value', ascending=False).reset_index(drop=True)
df_emission_mean_copy['variable'] = 'Mean total emission (万吨)'

# Mean net carbon emission from 2001 to 2017
df_net_mean_copy = pd.DataFrame(emission_mean_01 - flow_mean_copy * 100).reset_index()
df_net_mean_copy.columns = ['name', 'value']
df_net_mean_copy = df_net_mean_copy.sort_values(by='value', ascending=False).reset_index(drop=True)
df_net_mean_copy['variable'] = 'Mean net emission (万吨)'

# Mean total carbon emission per capita from 2001 to 2017
df_total_01_perCap_mean_copy = pd.DataFrame(df_total_01_perCap.iloc[:, 1:].mean(axis=0)).reset_index()
df_total_01_perCap_mean_copy.columns = ['name', 'value']
df_total_01_perCap_mean_copy = df_total_01_perCap_mean_copy.sort_values(by='value', ascending=False).reset_index(drop=True)
df_total_01_perCap_mean_copy['variable'] = 'Mean total emission per capita (万吨/人)'

# Mean total carbon emission per total GDP from 2001 to 2017
df_total_01_gdpTotal_mean_copy = pd.DataFrame(df_total_01_gdpTotal.iloc[:, 1:].mean(axis=0)).reset_index()
df_total_01_gdpTotal_mean_copy.columns = ['name', 'value']
df_total_01_gdpTotal_mean_copy = df_total_01_gdpTotal_mean_copy.sort_values(by='value', ascending=False).reset_index(drop=True)
df_total_01_gdpTotal_mean_copy['variable'] = 'Mean total emission per total GDP (万吨/亿元)'

# Mean net carbon emission per capita from 2001 to 2017
df_net_01_perCap_mean_copy = pd.DataFrame(df_net_01_perCap.iloc[:, 1:].mean(axis=0)).reset_index()
df_net_01_perCap_mean_copy.columns = ['name', 'value']
df_net_01_perCap_mean_copy = df_net_01_perCap_mean_copy.sort_values(by='value', ascending=False).reset_index(drop=True)
df_net_01_perCap_mean_copy['variable'] = 'Mean net emission per capita (万吨/人)'

# Mean net carbon emission per total GDP from 2001 to 2017
df_net_01_gdpTotal_mean_copy = pd.DataFrame(df_net_01_gdpTotal.iloc[:, 1:].mean(axis=0)).reset_index()
df_net_01_gdpTotal_mean_copy.columns = ['name', 'value']
df_net_01_gdpTotal_mean_copy = df_net_01_gdpTotal_mean_copy.sort_values(by='value', ascending=False).reset_index(drop=True)
df_net_01_gdpTotal_mean_copy['variable'] = 'Mean net emission per total GDP (万吨/亿元)'

# Unify mean total and net carbon emission
df_total_net_mean_emission_01 = pd.concat([df_emission_mean_copy, df_net_mean_copy, df_total_01_perCap_mean_copy, df_total_01_gdpTotal_mean_copy, df_net_01_perCap_mean_copy, df_net_01_gdpTotal_mean_copy], axis=0)

Ranking of __mean__ carbon emission from 2001 to 2017 

In [24]:
# Visualization function
def f(order):

    df = df_total_net_mean_emission_01.dropna()
    df = df.sort_values(by=['variable', 'value']).reset_index(drop=True).reset_index()

    var_order = sorted(list(set(df.variable)))
    category_orders = {'name': df.name[(var_order.index(order)*30):((var_order.index(order)+1)*30)].values[::-1]} 

    fig = px.bar(df, y='name', x='value', color='variable', barmode='group', orientation='h', category_orders=category_orders, height=800)

    fig.update_yaxes(title_text='Descending order by {}'.format(order))
    fig.update_layout(title_text="Mean Carbon Emission 2001-2017", title_x=0.5)
    fig.show()

year = widgets.IntSlider(
    value=2017,
    min=2001,
    max=2017,
    step=1,
    description='year',
    disabled=False,
    continuous_update=False,
    orientation='horizontal',
    readout=True,
    readout_format='d'
)

a = interact(f, order=sorted(list(set(df_total_net_mean_emission_01.variable))))

interactive(children=(Dropdown(description='order', options=('Mean net emission (万吨)', 'Mean net emission per …

In [25]:
# Data pre-processing 
# Total carbon emission
df_emission_01_copy = df_emission_01.melt(id_vars=['year'])
df_emission_01_copy.columns = ['year', 'name', 'value']
df_emission_01_copy['variable'] = 'Total emission (万吨)'

# Net carbon emission
df_net_01_copy = df_net_01.melt(id_vars=['year'])
df_net_01_copy.columns = ['year', 'name', 'value']
df_net_01_copy['variable'] = 'Net emission (万吨)'

# total carbon emission per capita from 2001 to 2017
df_total_01_perCap_copy = df_total_01_perCap.melt(id_vars=['year'])
df_total_01_perCap_copy.columns = ['year', 'name', 'value']
df_total_01_perCap_copy['variable'] = 'Total emission per capita (万吨/人)'

# total carbon emission per total GDP from 2001 to 2017
df_total_01_gdpTotal_copy = df_total_01_gdpTotal.melt(id_vars=['year'])
df_total_01_gdpTotal_copy.columns = ['year', 'name', 'value']
df_total_01_gdpTotal_copy['variable'] = 'Total emission per total GDP (万吨/亿元)'

# net carbon emission per capita from 2001 to 2017
df_net_01_perCap_copy = df_net_01_perCap.melt(id_vars=['year'])
df_net_01_perCap_copy.columns = ['year', 'name', 'value']
df_net_01_perCap_copy['variable'] = 'Net emission per capita (万吨/人)'

# net carbon emission per total GDP from 2001 to 2017
df_net_01_gdpTotal_copy = df_net_01_gdpTotal.melt(id_vars=['year'])
df_net_01_gdpTotal_copy.columns = ['year', 'name', 'value']
df_net_01_gdpTotal_copy['variable'] = 'Net emission per total GDP (万吨/亿元)'

# Unify total and net carbon emission
df_total_net_emission_01 = pd.concat([df_emission_01_copy, df_net_01_copy, df_total_01_perCap_copy, df_total_01_gdpTotal_copy, df_net_01_perCap_copy, df_net_01_gdpTotal_copy], axis=0)
# df_total_net_emission_01

Ranking of __annual__ carbon emission

In [26]:
def f(year, order):

    df = df_total_net_emission_01[df_total_net_emission_01['year']==year].dropna()
    df = df.sort_values(by=['variable', 'value']).reset_index(drop=True).reset_index()

    var_order = sorted(list(set(df.variable)))
    category_orders = {'name': df.name[(var_order.index(order)*30):((var_order.index(order)+1)*30)].values[::-1]} 

    fig = px.bar(df, y='name', x='value', color='variable', barmode='group', orientation='h', category_orders=category_orders, height=800)
    fig.update_yaxes(title_text='Descending order by {}'.format(order))
    fig.update_layout(title_text="Total and Net Carbon Emission in {}".format(year),title_x=0.5)
    fig.show()

year = widgets.IntSlider(
    value=2017,
    min=2001,
    max=2017,
    step=1,
    description='year',
    disabled=False,
    continuous_update=False,
    orientation='horizontal',
    readout=True,
    readout_format='d'
)

a = interact(f, year=year, order=sorted(list(set(df_total_net_emission_01.variable))))

interactive(children=(IntSlider(value=2017, continuous_update=False, description='year', max=2017, min=2001), …

## Carbon + Census


In [27]:
# Query GDP and GDP per capita from 2000 to 2017
START_YEAR = 2000
END_YEAR = 2017
df_gdp = df_PP_copy.loc[(df_PP_copy['lv4']=='人均地区生产总值(元per人)') | (df_PP_copy['lv4']=='地区生产总值(亿元)') & (df_PP_copy['year']<=END_YEAR) & (df_PP_copy['year']>=START_YEAR), df_PP_copy.columns[4:]]

# Pull information from difference sources together
gdpPp_mean = df_gdp.loc[df_PP['lv4']=='人均地区生产总值(元per人)', df_PP_copy.columns[6:]].mean(axis=0)
gdpTotal_mean = df_gdp.loc[df_PP['lv4']=='地区生产总值(亿元)', df_PP_copy.columns[6:]].mean(axis=0)
carbon_gdp_mean = pd.concat([gdpTotal_mean, gdpPp_mean, sink_mean_copy, emission_mean_copy], axis=1)
carbon_gdp_mean = carbon_gdp_mean.reset_index()
carbon_gdp_mean.columns = ['name', 'total', 'perCap', 'sink', 'emission']
# carbon_gdp_mean.head(5)

### Bubble plot

In [29]:
pd.options.mode.chained_assignment = None  # default='warn
# Standardize field names
df_emission_copy.insert(0, 'variable', ['碳指标-总排放（万吨CO2）']*df_emission_copy.shape[0])
df_sink_copy.insert(0, 'variable', ['碳指标-碳汇 （百万吨）']*df_sink_copy.shape[0])
df_flow_copy.insert(0, 'variable', ['碳指标-碳吸收（百万吨）']*df_flow_copy.shape[0])
df_net_01.insert(0, 'variable', ['碳指标-净排放（万吨）']*df_net_01.shape[0])
df_net_01_perCap.insert(0, 'variable', ['碳指标-人均净排放（万吨/人）']*df_net_01_perCap.shape[0])
df_net_01_gdpTotal.insert(0, 'variable', ['碳指标-净排放/生产总值（万吨/亿元）']*df_net_01_gdpTotal.shape[0])
df_total_all_perCap.insert(0, 'variable', ['碳指标-人均总排放（万吨/人）']*df_total_all_perCap.shape[0])
df_total_all_gdpTotal.insert(0, 'variable', ['碳指标-总排放/生产总值（万吨/亿元）']*df_total_all_gdpTotal.shape[0])

df_PP_copy = df_PP_copy[df_PP_copy.columns[5:]]
df_PP_copy.insert(0, 'variable', df_PP[['lv1', 'lv4']].agg('-'.join, axis=1))

In [30]:
# Combine carbon and GDP into one dataframe
df_PP_carbon_copy = pd.concat([df_PP_copy, df_sink_copy, df_emission_copy, df_flow_copy, df_net_01, df_net_01_perCap, df_net_01_gdpTotal, df_total_all_perCap, df_total_all_gdpTotal], axis=0)
fids_all = list(sorted(set(df_PP_carbon_copy.variable)))
# df_PP_carbon_copy

__Annual__ vsualization with limits fixed

In [31]:
pd.options.mode.chained_assignment = None  # default='warn

def select_df(df, var, label):
    try:
        df_clip = df.loc[df['variable']==var]
        df_clip.loc[df_clip['variable']==var, 'variable'] = label
    except:
        for idx, item in enumerate([i for i in df.columns]):
            if 'var' in item:
                df.columns = df.columns.drop(item).insert(idx, 'variable')
                df_clip = df.loc[df['variable']==var]
                df_clip.loc[df_clip['variable']==var, 'variable'] = label
    return df_clip

def map_carbon_plus(year, x, y, size, color, size_max):
    # Select and pull information from difference sources together
    # For now select based on year and lv1-lv4 indicators
    # 1. Selection based on lv4 variables
    df_x = select_df(df_PP_carbon_copy, x, 'x')
    cols = df_x.columns.drop(['variable', 'year'])
    df_x[cols] = df_x[cols].apply(pd.to_numeric, errors='coerce')
    df_x_np = df_x.loc[df_x['variable']=='x', df_x.columns.drop(['variable', 'year'])].to_numpy()
    xaxis_range = [df_x_np[~np.isnan(df_x_np)].min(), df_x_np[~np.isnan(df_x_np)].max()]
    
    df_y = select_df(df_PP_carbon_copy, y, 'y')
    cols = df_y.columns.drop(['variable', 'year'])
    df_y[cols] = df_y[cols].apply(pd.to_numeric, errors='coerce')
    df_y_np = df_y.loc[df_y['variable']=='y', df_y.columns.drop(['variable', 'year'])].to_numpy()
    yaxis_range = [df_y_np[~np.isnan(df_y_np)].min(), df_y_np[~np.isnan(df_y_np)].max()]
    
    df_size = select_df(df_PP_carbon_copy, size, 'size')
    df_color = select_df(df_PP_carbon_copy, color, 'color')
    df_carbon_plus = pd.concat([df_x, df_y, df_size, df_color])

    # Selection based on year
    df_carbon_plus = df_carbon_plus.loc[df_carbon_plus['year']==year]
    df_carbon_plus = df_carbon_plus[df_carbon_plus.columns.drop('year')]
    df_carbon_plus.columns = df_carbon_plus.columns.drop('variable').insert(0, 'var')
    
    # Orgnize dataframe
    df_carbon_plus = df_carbon_plus.melt(id_vars=['var'])
    df_carbon_plus.columns = ['variable', 'name', 'value']

    df_carbon_plus['value'] = df_carbon_plus['value'].apply(pd.to_numeric, errors='coerce')
    df_carbon_plus = df_carbon_plus.pivot(index='name', columns='variable')['value'].reset_index()
    df_carbon_plus = df_carbon_plus.dropna()
    
    # Plot
    fig = px.scatter(df_carbon_plus, x='x', y='y', text='name', size='size', color='color', 
                    hover_name='name', size_max=size_max, color_continuous_scale='matter',
                     labels={"x": x, "y": y, "size": size, "color": color}, trendline="ols") # size_max -> ???
    
    fig.update_xaxes(title_text=x)
    fig.update_yaxes(title_text=y)
    fig.update_traces(textposition='top right')
    fig.update_layout(coloraxis_colorbar=dict(title=color))
    fig.update_layout(xaxis_range=xaxis_range, yaxis_range=yaxis_range)

    fig.show()

year = widgets.IntSlider(
    value=2017,
    min=1995,
    max=2017,
    step=1,
    description='Year',
    disabled=False,
    continuous_update=False,
    orientation='horizontal',
    readout=True,
    readout_format='d'
)
x = widgets.Dropdown(options= fids_all, value='国民经济核算-地区生产总值(亿元)', description='x', disabled=False)
y = widgets.Dropdown(options= fids_all, value='国民经济核算-人均地区生产总值(元per人)', description='y', disabled=False)
size = widgets.Dropdown(options= fids_all, value='碳指标-碳汇 （百万吨）', description='size', disabled=False)
color = widgets.Dropdown(options= fids_all, value='碳指标-总排放（万吨CO2）', description='color', disabled=False)
size_max = widgets.IntSlider(
    value=30,
    min=10,
    max=100,
    step=5,
    description='maximum size',
    disabled=False,
    continuous_update=False,
    orientation='horizontal',
    readout=True,
    readout_format='d'
)

interact(map_carbon_plus, year=year, x=x, y=y, size=size, color=color, size_max=size_max)


interactive(children=(IntSlider(value=2017, continuous_update=False, description='Year', max=2017, min=1995), …

<function __main__.map_carbon_plus>

__Annual__ vsualization with limits flexible

In [32]:
pd.options.mode.chained_assignment = None  # default='warn

def select_df(df, var, label):
    try:
        df_clip = df.loc[df['variable']==var]
        df_clip.loc[df_clip['variable']==var, 'variable'] = label
    except:
        for idx, item in enumerate([i for i in df.columns]):
            if 'var' in item:
                df.columns = df.columns.drop(item).insert(idx, 'variable')
                df_clip = df.loc[df['variable']==var]
                df_clip.loc[df_clip['variable']==var, 'variable'] = label
    return df_clip

def map_carbon_plus(year, x, y, size, color, size_max):
    # Select and pull information from difference sources together
    # For now select based on year and lv1-lv4 indicators
    # 1. Selection based on lv4 variables
    df_carbon_plus = pd.concat([select_df(df_PP_carbon_copy, x, 'x'), select_df(df_PP_carbon_copy, y, 'y'), select_df(df_PP_carbon_copy, size, 'size'), select_df(df_PP_carbon_copy, color, 'color')])
    
    # Selection based on year
    df_carbon_plus = df_carbon_plus.loc[df_carbon_plus['year']==year]
    df_carbon_plus = df_carbon_plus[df_carbon_plus.columns.drop('year')]
    df_carbon_plus.columns = df_carbon_plus.columns.drop('variable').insert(0, 'var')
    
    # Orgnize dataframe
    df_carbon_plus = df_carbon_plus.melt(id_vars=['var'])
    df_carbon_plus.columns = ['variable', 'name', 'value']

    df_carbon_plus['value'] = df_carbon_plus['value'].apply(pd.to_numeric, errors='coerce')
    df_carbon_plus = df_carbon_plus.pivot(index='name', columns='variable')['value'].reset_index()
    df_carbon_plus = df_carbon_plus.dropna()
    
    # Plot
    fig = px.scatter(df_carbon_plus, x='x', y='y', text='name', size='size', color='color', 
                    hover_name='name', size_max=size_max, color_continuous_scale='matter',
                     labels={"x": x, "y": y, "size": size, "color": color}, trendline="ols") # size_max -> ???
    
    fig.update_xaxes(title_text=x)
    fig.update_yaxes(title_text=y)
    fig.update_traces(textposition='top right')
    fig.update_layout(coloraxis_colorbar=dict(title=color))

    fig.show()

year = widgets.IntSlider(
    value=2017,
    min=1995,
    max=2017,
    step=1,
    description='Year',
    disabled=False,
    continuous_update=False,
    orientation='horizontal',
    readout=True,
    readout_format='d'
)
x = widgets.Dropdown(options= fids_all, value='国民经济核算-地区生产总值(亿元)', description='x', disabled=False)
y = widgets.Dropdown(options= fids_all, value='国民经济核算-人均地区生产总值(元per人)', description='y', disabled=False)
size = widgets.Dropdown(options= fids_all, value='碳指标-碳汇 （百万吨）', description='size', disabled=False)
color = widgets.Dropdown(options= fids_all, value='碳指标-总排放（万吨CO2）', description='color', disabled=False)
size_max = widgets.IntSlider(
    value=30,
    min=10,
    max=100,
    step=5,
    description='maximum size',
    disabled=False,
    continuous_update=False,
    orientation='horizontal',
    readout=True,
    readout_format='d'
)

interact(map_carbon_plus, year=year, x=x, y=y, size=size, color=color, size_max=size_max)


interactive(children=(IntSlider(value=2017, continuous_update=False, description='Year', max=2017, min=1995), …

<function __main__.map_carbon_plus>

### Line plot

In [33]:
np.seterr(divide = 'ignore') 

def select_df(df, var, label):
    try:
        df_clip = df.loc[df['variable']==var]
        df_clip.loc[df_clip['variable']==var, 'variable'] = label
    except:
        for idx, item in enumerate([i for i in df.columns]):
            if 'var' in item:
                df.columns = df.columns.drop(item).insert(idx, 'variable')
                df_clip = df.loc[df['variable']==var]
                df_clip.loc[df_clip['variable']==var, 'variable'] = label
    return df_clip

def map_carbon_plus_allYear(x, y, log):

    df_x_y = pd.concat([select_df(df_PP_carbon_copy, x, 'x'), select_df(df_PP_carbon_copy, y, 'y')])
    df_x_y.columns = df_x_y.columns.drop('variable').insert(0, 'var')

    df_x_y = df_x_y.melt(id_vars=['var', 'year'])
    df_x_y.columns = ['variable', 'year', 'name', 'value']

    df_x_y = df_x_y.dropna()
    df_x_y['value'] = df_x_y['value'].apply(pd.to_numeric, errors='coerce')
    if log:
      df_x_y['value'] = np.log(df_x_y['value'])

    df_x_y = df_x_y.pivot(index=['name', 'year'], columns='variable', 
                          values='value').reset_index().rename_axis(None, axis=1)
#     print(df_x_y)

    # Plot
    fig = px.scatter(df_x_y, x='x', y='y', color='name', hover_name='name', text='year',
                     labels={"x": x, "y": y})
    
    fig.update_xaxes(title_text=x)
    fig.update_yaxes(title_text=y)
    fig.update_traces(textposition='top right')
    fig.update_traces(mode="markers+lines")

    fig.show()

x = widgets.Dropdown(options= fids_all, value='国民经济核算-人均地区生产总值(元per人)', description='x', disabled=False)
y = widgets.Dropdown(options= fids_all, value='碳指标-总排放（万吨CO2）', description='y', disabled=False)
log = widgets.Checkbox(value=False, description='Log Transformation')

interact(map_carbon_plus_allYear, x=x, y=y, log=log)


interactive(children=(Dropdown(description='x', index=1098, options=('人口-0-14岁人口数(人口抽样调查)(人)', '人口-15-64岁人口数(人…

<function __main__.map_carbon_plus_allYear>

## Spatial grouping

In [34]:
df_PP_carbon_copy_2 = df_PP_carbon_copy
df_PP_carbon_copy_2.columns = df_PP_carbon_copy_2.columns.drop('variable').insert(0, 'var')

In [35]:
df_PP_carbon_copy_2 = df_PP_carbon_copy_2.melt(id_vars=['var', 'year'])
df_PP_carbon_copy_2.columns = ['variable', 'year', 'name', 'value']
df_PP_carbon_copy_2['value'] = df_PP_carbon_copy_2['value'].apply(pd.to_numeric, errors='coerce')
# df_PP_carbon_copy_2

In [36]:
df_PP_carbon_group_copy = pd.merge(df_PP_carbon_copy_2, df_group_copy, how='outer', on=['name'])
# df_PP_carbon_group_copy

In [37]:
# Calculate mean or sum for each group
spatial_group_list = df_group_copy.columns.drop('name')

def group(df, spatial_group, math, other=['year', 'variable']):
    if math == 'sum':
        out = df.groupby(by=[spatial_group] + [i for i in other]).sum().reset_index()
    if math == 'mean':
        out = df.groupby(by=[spatial_group] + [i for i in other]).mean().reset_index()
    out.columns = out.columns.drop(spatial_group).insert(0, 'group')
    return out

# group(df_PP_carbon_group_copy, spatial_group_list[0], 'mean')

In [38]:
def main(df, math, spatial_group):
    out = group(df_PP_carbon_group_copy, spatial_group, math)
    out.columns = [spatial_group, 'year', 'variable', spatial_group+'_'+math]
    return pd.merge(df, out, 'outer', on=[spatial_group, 'year', 'variable'])

spatial_group_list = df_group_copy.columns.drop('name')

df_all = main(df_PP_carbon_group_copy, 'sum', spatial_group_list[0])
df_all = main(df_all, 'sum', spatial_group_list[1])
df_all = main(df_all, 'sum', spatial_group_list[2])
df_all = main(df_all, 'sum', spatial_group_list[3])
df_all = main(df_all, 'sum', spatial_group_list[4])
df_all = main(df_all, 'mean', spatial_group_list[0])
df_all = main(df_all, 'mean', spatial_group_list[1])
df_all = main(df_all, 'mean', spatial_group_list[2])
df_all = main(df_all, 'mean', spatial_group_list[3])
df_all = main(df_all, 'mean', spatial_group_list[4])
# df_all

In [39]:
# Harmonize province or district names with geojson dataset
df_names = list(set(df_all.name))
geo_idx = []
name_list_ = []
geo_name = []

for loc_idx, loc_name in enumerate(text):
    for df_idx, df_name in enumerate(df_names):
        if (loc_name in df_name) | (df_name in loc_name):
            geo_idx.append(loc_idx)
            name_list_.append(df_name)
            geo_name.append(loc_name)

df_geo_idx = pd.DataFrame({'geo_index': geo_idx, 'name': name_list_, 'geo_name': geo_name})
# df_geo_idx

In [40]:
df_all_copy = pd.merge(df_all, df_geo_idx, 'outer', on='name')
# df_all_copy

In [41]:
# df_all_copy.to_csv('/content/carbon-plus/data/all_in_one.csv', encoding='utf_8_sig')
# from google.colab import files
# files.download('/content/carbon-plus/data/all_in_one.csv') 

### Bubble plot

In [42]:
pd.options.mode.chained_assignment = None  # default='warn

def select_df(df, var, label):
    try:
        df_clip = df.loc[df['variable']==var]
        df_clip.loc[df_clip['variable']==var, 'variable'] = label
    except:
        for idx, item in enumerate([i for i in df.columns]):
            if 'var' in item:
                df.columns = df.columns.drop(item).insert(idx, 'variable')
                df_clip = df.loc[df['variable']==var]
                df_clip.loc[df_clip['variable']==var, 'variable'] = label
    return df_clip

def map_carbon_plus(year, x, y, size, color, size_max, spatial_group, math):
    # Select and pull information from difference sources together
    # For now select based on year and lv1-lv4 indicators
    # 1. Selection based on lv4 variables
    df_input = group(df_PP_carbon_group_copy, spatial_group, math)

    df_carbon_plus = pd.concat([select_df(df_input, x, 'x'), select_df(df_input, y, 'y'), select_df(df_input, size, 'size'), select_df(df_input, color, 'color')])

    # Selection based on year
    df_carbon_plus = df_carbon_plus.loc[df_carbon_plus['year']==year]
    df_carbon_plus = df_carbon_plus[df_carbon_plus.columns.drop('year')]
    df_carbon_plus.columns = ['label', 'variable', 'value']

    # Orgnize dataframe
    df_carbon_plus = df_carbon_plus.pivot(index='label', columns='variable')['value'].reset_index()
    df_carbon_plus = df_carbon_plus.dropna()
    cols = df_carbon_plus.columns.drop('label')
    df_carbon_plus[cols] = df_carbon_plus[cols].apply(pd.to_numeric, errors='coerce')
    
    # Plot
    fig = px.scatter(df_carbon_plus, x='x', y='y', text='label', size='size', color='color', 
                    hover_name='label', size_max=size_max, color_continuous_scale='matter',
                     labels={"x": x, "y": y, "size": size, "color": color}, trendline="ols") # size_max -> ???
    
    fig.update_xaxes(title_text=x)
    fig.update_yaxes(title_text=y)
    fig.update_traces(textposition='top right')
    fig.update_layout(coloraxis_colorbar=dict(title=color))

    fig.show()

    # Map
    if spatial_group == 'name':
        df = df_all_copy[(df_all_copy['year']==year) & (df_all_copy['variable']==x)][['name', 'value', 'geo_index']]
        group_names = [np.nan]*df.shape[0]
        df['group_name'] = group_names
    else: 
        df = df_all_copy[(df_all_copy['year']==year) & (df_all_copy['variable']==x)][['name', spatial_group+'_'+math, 'geo_index', spatial_group]]
        df.columns = ['name', 'value', 'geo_index', 'group_name']
    df['text'] = df["group_name"].astype(str) + '-' + df["name"]
    df = pd.merge(pd.DataFrame({'geo_index': np.arange(0, 34)}), df, 'outer', on='geo_index')
    df = df.set_index('geo_index').sort_index().reset_index()

    try:
        fig= go.Figure(go.Choroplethmapbox(z=df['value'],
                                  geojson=jdata,
                                  locations=df.geo_index,
                                  colorscale='greens',
                                  colorbar=dict(thickness=20, ticklen=3),
                                  text=df['text'],
                                  hoverinfo='all',
                                  marker_line_width=1, marker_opacity=0.75))

        fig.update_layout(title_text= '{}年 - {} - {}'.format(year, x, spatial_group),
                        title_x=0.5, width = 700,# height=700,
                        mapbox = dict(center= dict(lat=36.913818,  lon=106.363625),
                                        accesstoken= MAPBOX_TOKEN,
                                        style='basic',
                                        zoom=2.35,
                                      ));

        # fig.update_mapboxes(style='white-bg')
        fig.data[0].hovertemplate =  '<b>Label</b>: <b>%{text}</b>'+'<br> <b>Val </b>: %{z}<br>'
        fig.show()

    except:
        print('No data in {}'.format(year))

year = widgets.IntSlider(
    value=2017,
    min=1995,
    max=2017,
    step=1,
    description='Year',
    disabled=False,
    continuous_update=False,
    orientation='horizontal',
    readout=True,
    readout_format='d'
)
x = widgets.Dropdown(options= fids_all, value='国民经济核算-地区生产总值(亿元)', description='x', disabled=False)
y = widgets.Dropdown(options= fids_all, value='国民经济核算-人均地区生产总值(元per人)', description='y', disabled=False)
size = widgets.Dropdown(options= fids_all, value='碳指标-碳汇 （百万吨）', description='size', disabled=False)
color = widgets.Dropdown(options= fids_all, value='碳指标-总排放（万吨CO2）', description='color', disabled=False)
size_max = widgets.IntSlider(
    value=30,
    min=10,
    max=100,
    step=5,
    description='maximum size',
    disabled=False,
    continuous_update=False,
    orientation='horizontal',
    readout=True,
    readout_format='d'
)
spatial_group = widgets.Dropdown(options= spatial_group_list.to_list() + ['name'], value='name', description='Grouping scenario', disabled=False)
math = widgets.Dropdown(options= ['sum', 'mean'], value='mean', description='Aggregation algebra', disabled=False)

interact(map_carbon_plus, year=year, x=x, y=y, size=size, color=color, size_max=size_max, spatial_group=spatial_group, math=math)


interactive(children=(IntSlider(value=2017, continuous_update=False, description='Year', max=2017, min=1995), …

<function __main__.map_carbon_plus>

### Line plot

In [43]:
np.seterr(divide = 'ignore') 

def select_df(df, var, label):
    try:
        df_clip = df.loc[df['variable']==var]
        df_clip.loc[df_clip['variable']==var, 'variable'] = label
    except:
        for idx, item in enumerate([i for i in df.columns]):
            if 'var' in item:
                df.columns = df.columns.drop(item).insert(idx, 'variable')
                df_clip = df.loc[df['variable']==var]
                df_clip.loc[df_clip['variable']==var, 'variable'] = label
    return df_clip

def map_carbon_plus_allYear(x, y, log, spatial_group, math, year):
    df_input = group(df_PP_carbon_group_copy, spatial_group, math)

    df_x_y = pd.concat([select_df(df_input, x, 'x'), select_df(df_input, y, 'y')])
    df_x_y.columns = df_x_y.columns.drop('group').insert(0, 'label')
    df_x_y = df_x_y.dropna()

    df_x_y['value'] = df_x_y['value'].apply(pd.to_numeric, errors='coerce')
    if log:
        df_x_y['value'] = np.log(df_x_y['value'])

    df_x_y = df_x_y.pivot(index=['label', 'year'], columns='variable', 
                          values='value').reset_index().rename_axis(None, axis=1)

    # Plot
    fig = px.scatter(df_x_y, x='x', y='y', color='label', hover_name='label', text='year',
                     labels={"x": x, "y": y})
    
    fig.update_xaxes(title_text=x)
    fig.update_yaxes(title_text=y)
    fig.update_traces(textposition='top right')
    fig.update_traces(mode="markers+lines")
    fig.show()

    # Map
    if spatial_group == 'name':
        df = df_all_copy[(df_all_copy['year']==year) & (df_all_copy['variable']==x)][['name', 'value', 'geo_index']]
        group_names = [np.nan]*df.shape[0]
        df['group_name'] = group_names
    else: 
        df = df_all_copy[(df_all_copy['year']==year) & (df_all_copy['variable']==x)][['name', spatial_group+'_'+math, 'geo_index', spatial_group]]
        df.columns = ['name', 'value', 'geo_index', 'group_name']
    df['text'] = df["group_name"].astype(str) + '-' + df["name"]
    df = pd.merge(pd.DataFrame({'geo_index': np.arange(0, 34)}), df, 'outer', on='geo_index')
    df = df.set_index('geo_index').sort_index().reset_index()

    try:
        fig= go.Figure(go.Choroplethmapbox(z=df['value'],
                                  geojson=jdata,
                                  locations=df.geo_index,
                                  colorscale='greens',
                                  colorbar=dict(thickness=20, ticklen=3),
                                  text=df['text'],
                                  hoverinfo='all',
                                  marker_line_width=1, marker_opacity=0.75))

        fig.update_layout(title_text= '{}年 - {} - {}'.format(year, x, spatial_group),
                        title_x=0.5, width = 700,# height=700,
                        mapbox = dict(center= dict(lat=36.913818,  lon=106.363625),
                                        accesstoken= MAPBOX_TOKEN,
                                        style='basic',
                                        zoom=2.35,
                                      ));

        # fig.update_mapboxes(style='white-bg')
        fig.data[0].hovertemplate =  '<b>Label</b>: <b>%{text}</b>'+'<br> <b>Val </b>: %{z}<br>'
        fig.show()

    except:
        print('No data in {}'.format(year))

year = widgets.IntSlider(
    value=2017,
    min=1995,
    max=2017,
    step=1,
    description='Year',
    disabled=False,
    continuous_update=False,
    orientation='horizontal',
    readout=True,
    readout_format='d'
)

x = widgets.Dropdown(options= fids_all, value='国民经济核算-人均地区生产总值(元per人)', description='x', disabled=False)
y = widgets.Dropdown(options= fids_all, value='碳指标-总排放（万吨CO2）', description='y', disabled=False)
log = widgets.Checkbox(value=False, description='Log Transformation')
spatial_group = widgets.Dropdown(options= spatial_group_list.to_list() + ['name'], value='name', description='Grouping scenario', disabled=False)
math = widgets.Dropdown(options= ['sum', 'mean'], value='mean', description='Aggregation algebra', disabled=False)

a = interact(map_carbon_plus_allYear, x=x, y=y, log=log, spatial_group=spatial_group, math=math, year=year)


interactive(children=(Dropdown(description='x', index=1098, options=('人口-0-14岁人口数(人口抽样调查)(人)', '人口-15-64岁人口数(人…

### Map


In [44]:
def map_carbon(year, variable, spatial_group, math):
    if spatial_group == 'name':
        df = df_all_copy[(df_all_copy['year']==year) & (df_all_copy['variable']==variable)][['name', 'value', 'geo_index']]
        group_names = [np.nan]*df.shape[0]
        df['group_name'] = group_names
    else: 
        df = df_all_copy[(df_all_copy['year']==year) & (df_all_copy['variable']==variable)][['name', spatial_group+'_'+math, 'geo_index', spatial_group]]
        df.columns = ['name', 'value', 'geo_index', 'group_name']
    df['text'] = df["group_name"].astype(str) + '-' + df["name"]
    df = pd.merge(pd.DataFrame({'geo_index': np.arange(0, 34)}), df, 'outer', on='geo_index')
    df = df.set_index('geo_index').sort_index().reset_index()

    try:
        fig= go.Figure(go.Choroplethmapbox(z=df['value'],
                                  geojson=jdata,
                                  locations=df.geo_index,
                                  colorscale='greens',
                                  colorbar=dict(thickness=20, ticklen=3),
                                  text=df['text'],
                                  hoverinfo='all',
                                  marker_line_width=1, marker_opacity=0.75))


        fig.update_layout(title_text= '{}年 - {} '.format(year, variable),
                        title_x=0.5, width = 700,# height=700,
                        mapbox = dict(center= dict(lat=36.913818,  lon=106.363625),
                                        accesstoken= MAPBOX_TOKEN,
                                        style='basic',
                                        zoom=2.35,
                                      ));

        # fig.update_mapboxes(style='white-bg')

        fig.data[0].hovertemplate =  '<b>Label</b>: <b>%{text}</b>'+'<br> <b>Val </b>: %{z}<br>'
      
        fig.show()
#         print(df)
        
    except:
        print('No data in {}'.format(year))


year = widgets.IntSlider(
    value=2017,
    min=1995,
    max=2017,
    step=1,
    description='Year',
    disabled=False,
    continuous_update=False,
    orientation='horizontal',
    readout=True,
    readout_format='d'
)
variable = widgets.Dropdown(options= fids_all, value='国民经济核算-地区生产总值(亿元)', description='Variable', disabled=False)
spatial_group = widgets.Dropdown(options= spatial_group_list.to_list() + ['name'], value='name', description='Grouping scenario', disabled=False)
math = widgets.Dropdown(options= ['sum', 'mean'], value='mean', description='Aggregation algebra', disabled=False)

a = interact(map_carbon, year=year, variable=variable, spatial_group=spatial_group, math=math)


interactive(children=(IntSlider(value=2017, continuous_update=False, description='Year', max=2017, min=1995), …